In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from commando import ComManDo
from commando.evaluation import generate_figure, test_partial
import matplotlib.pyplot as plt
from mmd_wrapper import mmd_combine
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn import preprocessing

2022-06-21 22:45:37.203499: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-06-21 22:45:37.203538: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


Instructions for updating:
non-resource variables are not supported in the long term


In [3]:
np.random.seed(42)

In [4]:
dataset_name = 'MMD-MA'
modality_names = ['Modality 1', 'Modality 2']
data1 = np.loadtxt("../data/Unioncom/MMD/s1_mapped1.txt")
data2 = np.loadtxt("../data/Unioncom/MMD/s1_mapped2.txt")
type1 = np.loadtxt("../data/Unioncom/MMD/s1_type1.txt")
type2 = np.loadtxt("../data/Unioncom/MMD/s1_type2.txt")
type1 = type1.astype(np.int)
type2 = type2.astype(np.int)

# Labels
labels = [type1, type2]
features = [None, None]

# Preprocessing
data1 = preprocessing.scale(data1, axis=0)
data2 = preprocessing.scale(data2, axis=0)
dataset = [data1, data2]

# Utility
positivize = lambda X: [(1 + preprocessing.scale(1 + x)) / 2 for x in X]

In [5]:
# Reduced Priors
full_priors = np.eye(len(dataset[0]))

random_idx = np.random.choice(range(len(dataset[0])), int(.5 * len(dataset[0])), replace=False)
priors = np.zeros(len(dataset[0]))
priors[random_idx] = 1
half_priors = np.diag(priors)

none_priors = np.zeros((len(dataset[0]), len(dataset[0])))

# Vars
reduced_dim = 32
batch_size = 150
pca_dim = [64, 64]

# ComManDo

In [6]:
kwargs = {
    'output_dim': reduced_dim,
    'epoch_DNN': 2000,
    'log_DNN': 500,
    'use_early_stop': False,
    'batch_size': batch_size,
    'pca_dim': pca_dim,
}
cm = ComManDo(**kwargs)
cm_data = cm.fit_transform(dataset=dataset)
cm_data_half = ComManDo(**kwargs, P=half_priors, match_result=cm.match_result, PF_Ratio=.5).fit_transform(dataset=dataset)
cm_data_none = ComManDo(**kwargs, P=none_priors, match_result=cm.match_result, PF_Ratio=0).fit_transform(dataset=dataset)

use random seed: 666
Shape of Raw data
Dataset 0: (300, 2000)
Dataset 1: (300, 1000)
Device: cpu
---------------------------------
Find correspondence between Dataset 1 and Dataset 2
epoch:[500/2000] err:3.1758 alpha:0.4226
epoch:[1000/2000] err:1.9772 alpha:0.4832
epoch:[1500/2000] err:1.8549 alpha:0.5037
epoch:[2000/2000] err:1.8305 alpha:0.5156
Finished Matching!
---------------------------------
Train coupled autoencoders
epoch:[500/2000]: loss:0.684494
epoch:[1000/2000]: loss:0.454214
epoch:[1500/2000]: loss:0.394824
epoch:[2000/2000]: loss:0.384545
Finished Mapping!
---------------------------------
ComManDo Done!
Distance: 0.061810601968318224
Correspondence: 4.0265977119561285
Mapping: 30.693873611977324
Total: 34.78228192590177

use random seed: 666
Shape of Raw data
Dataset 0: (300, 2000)
Dataset 1: (300, 1000)
---------------------------------
Train coupled autoencoders
epoch:[500/2000]: loss:0.685551
epoch:[1000/2000]: loss:0.458838
epoch:[1500/2000]: loss:0.412051
epoch:[2

# Comparison Methods

In [7]:
# Unioncom
uc = ComManDo(project_mode='tsne', output_dim=reduced_dim)
uc_data = uc.fit_transform(dataset=positivize(dataset))

# NLMA
nlma_data, _ = mmd_combine(*dataset, method='maninetcluster', alignment='nonlinear manifold aln', num_dims=reduced_dim)
nlma_data_half, _ = mmd_combine(*dataset, method='maninetcluster', alignment='nonlinear manifold aln', num_dims=reduced_dim, corr=half_priors)

# LMA
lma_data, _, _ = mmd_combine(*dataset, method='maninetcluster', alignment='linear manifold', num_dims=reduced_dim)
lma_data_half, _, _ = mmd_combine(*dataset, method='maninetcluster', alignment='linear manifold', num_dims=reduced_dim, corr=half_priors)

# CCA
cca_data, _, _ = mmd_combine(*dataset, method='maninetcluster', alignment='cca', num_dims=reduced_dim)
cca_data_half, _, _ = mmd_combine(*dataset, method='maninetcluster', alignment='cca', num_dims=reduced_dim, corr=half_priors)

use random seed: 666
Shape of Raw data
Dataset 0: (300, 2000)
Dataset 1: (300, 1000)
Device: cpu
---------------------------------
Find correspondence between Dataset 1 and Dataset 2
epoch:[500/2000] err:3.1758 alpha:0.4226
epoch:[1000/2000] err:1.9772 alpha:0.4832
epoch:[1500/2000] err:1.8549 alpha:0.5037
epoch:[2000/2000] err:1.8305 alpha:0.5156
Finished Matching!
---------------------------------
Begin finding the embedded space
epoch:[10/100]: loss:1.301498, align_loss:0.099425
epoch:[20/100]: loss:1.147658, align_loss:0.079610
epoch:[30/100]: loss:1.113466, align_loss:0.092025
epoch:[40/100]: loss:1.066275, align_loss:0.100602
epoch:[50/100]: loss:0.973657, align_loss:0.076822
epoch:[60/100]: loss:0.884399, align_loss:0.077996
epoch:[70/100]: loss:0.946658, align_loss:0.077635
epoch:[80/100]: loss:0.865855, align_loss:0.076834
epoch:[90/100]: loss:0.919443, align_loss:0.086771
epoch:[100/100]: loss:0.903482, align_loss:0.074987
Done
---------------------------------
ComManDo Done!

# Figure Generation

In [8]:
#%%capture --no-display
# https://miro.medium.com/max/800/1*zm6zVTIEvf9uZ0cE4n0Ogg.png
integrated_data = np.array([
    cm_data, cm_data_half,
    nlma_data, nlma_data_half,
    lma_data, lma_data_half,
    cca_data, cca_data_half,
])
integrated_alg_names = np.array([
    'JAMIE [Full Priors]', 'JAMIE [Half Priors]',
    'Nonlinear Manifold\nAlignment [Full]', 'Nonlinear Manifold\nAlignment [Half]',
    'Linear Manifold\nAlignment [Full]', 'Linear Manifold\nAlignment [Half]',
    'CCA [Full]', 'CCA [Half]',
])
integrated_alg_shortnames = np.array([
    'JAMIE [Full]', 'JAMIE [Half]',
    'NLMA [Full]', 'NLMA [Half]',
    'LMA [Full]', 'LMA [Half]',
    'CCA [Full]', 'CCA [Half]',
])
colors = np.array([
    'blue', 'lightblue',
    'red', 'lightcoral',
    'green', 'lightgreen',
    'm', 'violet',
])
alg_groups = np.zeros(len(integrated_data))
alg_groups[1::2] = 1
idx = range(len(integrated_data))
params = {
    'dataset_names': modality_names,
    'feature_names': [f if dim is None else None for dim, f in zip(pca_dim, features)] if pca_dim is not None else 2*[None],
    'integrated_data': integrated_data[idx],
    'integrated_alg_names': integrated_alg_names[idx],
    'integrated_alg_shortnames': integrated_alg_shortnames[idx],
    'colors': colors[idx],
    'alg_groups': alg_groups[idx],
    'raw_data_group': 0,
    'scale': 20,
    # 'dpi': 100,
    'integrated_use_pca': True,
}
generator = generate_figure(cm, dataset, labels, **params)
generator.plot(
    (
        lambda x: generator._plot_raw_data(x, ps_scale=.5),
        lambda x: generator._group_plot(x, generator._plot_integrated_data),
        generator._plot_accuracy_metrics,
        generator._plot_silhouette_value_boxplots,
        generator._plot_reconstruct_modality,
        generator._plot_auroc,
    ),
    (
        generator._get_raw_data_shape(),
        generator._group_shape(generator._get_integrated_data_shape()),
        generator._get_accuracy_metrics_shape(),
        generator._get_silhouette_value_boxplots_shape(),
        generator._get_reconstruct_modality_shape(),
        generator._get_auroc_shape(),
    ),
)
generator.get_fig().savefig('./output_figures/' + dataset_name + '.png')